In [0]:
# Credentials
storage_account_name = "datalakecineanalytics" 
client_id = "client_id"
tenant_id = "my_tentant_id"
client_secret = "my_client_key"

spark.conf.set(f"fs.azure.account.auth.type.{storage_account_name}.dfs.core.windows.net", "OAuth")
spark.conf.set(f"fs.azure.account.oauth.provider.type.{storage_account_name}.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set(f"fs.azure.account.oauth2.client.id.{storage_account_name}.dfs.core.windows.net", client_id)
spark.conf.set(f"fs.azure.account.oauth2.client.secret.{storage_account_name}.dfs.core.windows.net", client_secret)
spark.conf.set(f"fs.azure.account.oauth2.client.endpoint.{storage_account_name}.dfs.core.windows.net", f"https://login.microsoftonline.com/{tenant_id}/oauth2/token")

print("authentication configured")

✅ Authentication configured successfully!


In [0]:
# Information and credentials for datalake
storage_account_name = "datalakecineanalytics"
account_key = "my_account_key" 

# Key for DataBricks Workspace to use our Data Lake
spark.conf.set(
    f"fs.azure.account.key.{storage_account_name}.dfs.core.windows.net",
    account_key
)

# Setting Auto Loader Paths
catalog = "hive_metastore"
target_schema = "bronze"
source_path = f"abfss://bronze@{storage_account_name}.dfs.core.windows.net/"
checkpoint_base = f"abfss://bronze@{storage_account_name}.dfs.core.windows.net/checkpoints/"
schema_base = f"abfss://bronze@{storage_account_name}.dfs.core.windows.net/checkpoints/schemas/"

print("Data Lake Connection Established")

✅ Data Lake Connection Successfully Established!


In [ ]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, LongType 

In [0]:

# Creating ingest function for bronze layer
def ingest_bronze(df, table_name):
    full_table_name = f"{catalog}.{target_schema}.{table_name}"
    checkpoint_path = f"{checkpoint_base}{table_name}"
    
    (df.writeStream
        .format("delta")
        .option("checkpointLocation", checkpoint_path)
        .outputMode("append")
        .trigger(availableNow=True) 
        .toTable(full_table_name))

In [0]:


# Ingest Top Movies
top_movies_schema_path = f"{schema_base}top_movies_raw"

df_raw_movies = (spark.readStream
    .format("cloudFiles")
    .option("cloudFiles.format", "csv")
    .option("cloudFiles.allowOverwrites", "true")
    .option("cloudFiles.inferColumnTypes", "true")
    .option("cloudFiles.schemaLocation", top_movies_schema_path)
    .option("header", "true")
    .option("quote", "\"")
    .option("escape", "\"")
    .option("multiLine", "true")
    .option("pathGlobFilter", "Top Movies (Raw Data).csv") 
    .load(source_path)) 

new_cols = [c.replace(" ", "").replace(":", "").replace("/", "").replace(".", "") for c in df_raw_movies.columns]
df_raw_movies = df_raw_movies.toDF(*new_cols)

ingest_bronze(df_raw_movies, "top_movies_raw")

In [0]:

# MovieLens Ratings
schema_ratings = StructType([
    StructField("UserID", IntegerType(), True),
    StructField("MovieID", IntegerType(), True),
    StructField("Rating", IntegerType(), True),
    StructField("Timestamp", LongType(), True)
])

df_ratings = (spark.readStream
    .format("cloudFiles")
    .option("cloudFiles.format", "csv")
    .option("cloudFiles.allowOverwrites", "true")
    .option("sep", "::")
    .schema(schema_ratings)
    .option("pathGlobFilter", "ratings.dat")
    .load(source_path))

ingest_bronze(df_ratings, "ratings")

In [0]:

# MovieLens users
schema_users = StructType([
    StructField("UserID", IntegerType(), True),
    StructField("Gender", StringType(), True),
    StructField("Age", IntegerType(), True),
    StructField("Occupation", IntegerType(), True),
    StructField("Zip_code", StringType(), True)
])
df_users = (spark.readStream
    .format("cloudFiles")
    .option("cloudFiles.format", "csv")
    .option("cloudFiles.allowOverwrites", "true")
    .option("sep", "::")
    .schema(schema_users)
    .option("pathGlobFilter", "users.dat")
    .load(source_path))
ingest_bronze(df_users, "users")

In [0]:


# MovieLens Movies 
schema_movies = StructType([
    StructField("MovieID", IntegerType(), True),
    StructField("Title", StringType(), True),
    StructField("Genres", StringType(), True)
])

df_movies = (spark.readStream
    .format("cloudFiles")
    .option("cloudFiles.format", "csv")
    .option("cloudFiles.allowOverwrites", "true")
    .option("sep", "::")
    .schema(schema_movies)
    .option("pathGlobFilter", "movies.dat")
    .load(source_path))

ingest_bronze(df_movies, "movies")

# Links & Themes 
def ingest_simple(filename, table_name):
    table_schema_path = f"{schema_base}{table_name}"
    
    df = (spark.readStream
        .format("cloudFiles")
        .option("cloudFiles.format", "csv")
        .option("cloudFiles.allowOverwrites", "true")
        .option("cloudFiles.inferColumnTypes", "true")
        .option("cloudFiles.schemaLocation", table_schema_path) 
        .option("header", "true")
        .option("pathGlobFilter", filename)
        .load(source_path))
    
    ingest_bronze(df, table_name)

ingest_simple("links.csv", "links")
ingest_simple("movies_with_themes.csv", "movie_themes")

print("Incremental bronze ingestion done")

Incremental Bronze Ingestion Complete.


In [0]:
# Ingest TMDB Credits (Cast & Crew)
credits_schema_path = f"{schema_base}tmdb_credits_raw"

df_credits = (spark.readStream
    .format("cloudFiles")
    .option("cloudFiles.format", "csv")
    .option("cloudFiles.allowOverwrites", "true")
    .option("cloudFiles.inferColumnTypes", "true")
    .option("cloudFiles.schemaLocation", credits_schema_path)
    .option("header", "true")
    .option("quote", "\"")
    .option("escape", "\"")
    .option("multiLine", "true")
    .option("pathGlobFilter", "tmdb_5000_credits.csv")
    .load(source_path))

# Cleaning the columns
new_cols = [c.replace(" ", "").replace(":", "").replace("/", "").replace(".", "") for c in df_credits.columns]
df_credits = df_credits.toDF(*new_cols)

ingest_bronze(df_credits, "tmdb_credits_raw")
print("Bronze Layer - TMDB Credits ingested")

Bronze Layer: TMDB Credits Ingested.


In [0]:
%sql
SELECT * FROM hive_metastore.bronze.top_movies_raw

Unnamed0 ReleaseDate Movie ProductionBudget DomesticGross WorldwideGross MovieURL DomesticBoxOffice InternationalBoxOffice WorldwideBoxOffice EstDomesticDVDSales EstDomesticBlu-raySales TotalEstDomesticVideoSales Opening Weekend Legs DomesticShare Production Budget Theatercounts InflAdjDomBO DomesticReleases InternationalReleases Video Release MPAA Rating RunningTime Franchise Comparisons Keywords Source Genre Production Method Creative Type ProductionFinancingCompanies ProductionCountries Languages _rescued_data 1 16-Dec-15 Star Wars Ep. VII: The Force Awakens $533,200,000 $936,662,225 $2,056,046,835 https://www.the-numbers.com/movie/Star-Wars-Ep-VII-The-Force-Awakens#tab=summary $936,662,225 $1,119,384,610 $2,056,046,835 $39,601,100 $151,559,711 $191,160,811 $247,966,675 (26.5% of total gross) 3.78 (domestic box office/biggest weekend) 45.6% (domestic box office/worldwide) $533,200,000 (worldwide box office is 3.9 times production budget) 4,134 opening theaters/4,134 max. theaters, 9.2 weeks average run per theater $1,191,447,782 December 18th, 2015 (IMAX) byWalt DisneyDecember 18th, 2015 (Wide) byWalt Disney December 16th, 2015 (Wide) (Belgium)December 16th, 2015 (Wide) (Denmark)December 16th, 2015 (Wide) (Egypt)December 16th, 2015 (Wide) (Finland)December 16th, 2015 (Wide) (France)... Show all releases April 1st, 2016 byDisney/Lucasfilm PG-13for sci-fi action violence.(Rating bulletin 2401 (Cert #50155), 11/25/2015) 136 minutes Star Wars All-Time Top-Grossing FilmsBlockbusters, 2015vs. AvatarCreate your own comparison chart… Space Opera,Good vs. Evil,Delayed Sequel,Intertitle,Robot,Sequels With Returning Stars,Dysfunctional Family,Gratuitous Cameos,Motion Capture Performance,3-D,3-D - Post-production Conversion,IMAX: DMR,Filmed in England,Filmed in Pinewood Studios, Buckinghamshire, England,Filmed in Iceland,Filmed in the United Arab Emirates,Filmed in Liwa Oasis, Abu Dhabi,Filmed in Ireland,Filmed in Skellig Michael, Ireland,Filmed in County Kerry, Ireland,Filmed in the Lake District, England,Filmed in RAF Greenham Common, Berkshire, England,Filmed in Berkshire, England,Filmed in the Forest of Dean, Gloucestershire, England,Filmed in Puzzlewood, Gloucestershire, England,Filmed in United Kingdom,Filmed in Gloucestershire, England,Filmed in Abu Dhabi,Filmed in Buckinghamshire England,Filmed in United Arab Emirates,Heroic Adventure Original Screenplay Adventure Animation/Live Action Science Fiction Lucasfilm,Bad Robot United States English null 2 9-Dec-22 Avatar: The Way of Water $460,000,000 $684,075,767 $2,315,589,775 https://www.the-numbers.com/movie/Avatar-The-Way-of-Water-(2022)#tab=summary $684,075,767 $1,631,514,008 $2,315,589,775 $7,771,432 $11,365,092 $19,136,524 $134,100,226 (19.6% of total gross) 5.10 (domestic box office/biggest weekend) 29.5% (domestic box office/worldwide) $460,000,000 (worldwide box office is 5.0 times production budget) 4,202 opening theaters/4,340 max. theaters, 11.1 weeks average run per theater $693,596,368 December 16th, 2022 (Wide) by20th Century StudiosDecember 16th, 2022 (IMAX) by20th Century Studios December 9th, 2022 (Wide) (Finland)December 14th, 2022 (Wide), released asAvatar 2: The Way of Water(Austria)December 14th, 2022 (Wide) (Belgium)December 14th, 2022 (Wide), released asAvatar: The Way of Water (阿凡达：水之道)(China)December 14th, 2022 (Wide) (Denmark)... Show all releases March 28th, 2023 byWalt Disney Home Entertainment PG-13for sequences of strong violence and intense action, partial nudity and some strong language.(Rating bulletin 2759 (cert #54081), 11/23/2022) 190 minutes Avatar All-Time Top-Grossing Filmsvs. AvatarCreate your own comparison chart… Action Adventure,Delayed Sequel,Humans as Aliens,Sequel With Returning Stars Playing New Characters,2023 Oscars Best Picture Nominee,Filmed in Los Angeles, CA Original Screenplay Action Animation/Live Action Science Fiction Lightstorm Entertainment,20th Century Studios,TSG Entertainment United States English null 3 28-Jun-23 India